In [1]:
# IMPORT STATEMENTS
import math
import numpy as np
import pandas as pd

import os
import sys
sys.path.insert(0, "/Users/rohan/public_html/Hegemon/Data2/Data")
from moreprocessing import *
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu

Data processing for other databases: Usually, there are two files, expression counts and metadata.

Data source: https://egidexpress.research.cchmc.org/data/

In [14]:
# RPKM values
expr = pd.DataFrame(pd.read_csv("EoEtranscriptome.csv", sep = ",", header=0))
expr = expr.drop(["Unnamed: 0", "locus"], axis=1)
genes = expr.pop("gene_id")
expr.columns = [i.split("X")[1] for i in list(expr.columns)]
expr.insert(0, 'Name', genes)
expr.insert(0, 'ProbeID', genes)
expr

ProbeID    Name        168        461        508        520        527  \
0      ACTL6A  ACTL6A  12.538000  15.641600  13.586300  15.310400  16.369900   
1      ARID1A  ARID1A  12.055300  10.514500   9.780060  14.559200  13.942500   
2       BAZ1B   BAZ1B   5.546250   6.021250   6.345060   7.992120   7.242120   
3       CALB1   CALB1   0.000000   0.000000   0.000000   0.129677   0.009238   
4        CAMP    CAMP   0.000000   0.000000   0.000000   0.000000   0.000000   
...       ...     ...        ...        ...        ...        ...        ...   
31661  ZYG11A  ZYG11A   0.955795   0.655018   0.852525   0.729395   0.809126   
31662  ZYG11B  ZYG11B   3.901830   3.745230   4.319290   5.501440   3.407660   
31663     ZYX     ZYX  13.799700  17.570600  15.416700  14.987800  20.212800   
31664   ZZEF1   ZZEF1   4.076160   3.790990   3.991290   5.183870   4.557710   
31665    ZZZ3    ZZZ3   4.893700   4.940050   5.166090   6.145090   6.030240   

             609        333        334        424        513        594  \
0      15.143700  18.724500  24.118000  24.358100  34.308200  20.902100   
1      12.905600  15.842700  16.038200  16.927700  18.507400  23.365600   
2       4.942410   7.797820   8.519840  10.764200  12.902100  11.317600   
3       0.020548   0.000000   0.017173   0.022144   0.032969   0.000000   
4       0.000000   0.000000   0.000000   0.000000   0.000000   0.000000   
...          ...        ...        ...        ...        ...        ...   
31661   0.957145   0.376902   0.224454   0.130862   0.100365   0.186814   
31662   4.184400   3.606210   3.595670   3.857010   5.588660   5.627470   
31663  12.471500  21.793800  29.699600  31.803800  38.292700  29.169900   
31664   3.155660   5.372450   6.643050   6.361670   5.599140   7.981430   
31665   5.700290   6.710940   6.523000   7.696500   9.013630   7.796110   

             692        713        723        778        803  
0      26.157800  21.496500  25.741400  25.035500  23.115100  
1      14.782900  19.708500   9.864620  13.985800  12.474300  
2       8.459030  11.238300   7.851490   9.784140   8.937340  
3       0.035832   0.014727   0.037758   0.043798   0.086126  
4       0.297579   0.053123   0.000000   0.118364   0.000000  
...          ...        ...        ...        ...        ...  
31661   0.126172   0.100764   0.293117   0.095194   0.195846  
31662   4.641030   5.935930   5.312080   5.182140   5.692290  
31663  15.362600  21.067000   9.438700  16.460400  13.742400  
31664   5.480170   7.850140   4.625630   6.781950   6.515180  
31665   8.248420   7.426170   8.598290   7.928860   7.742580  

[31666 rows x 18 columns]

In [25]:
# Log transform expr values

genes = expr.loc[:,["ProbeID", "Name"]]
cols = expr.columns

# Normalize and log transform
expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
#sc.pp.normalize_total(df, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols

expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID    Name       168       461       508       520       527  \
0      ACTL6A  ACTL6A  3.758943  4.056722  3.866542  4.027720  4.118517   
1      ARID1A  ARID1A  3.706563  3.525380  3.430293  3.959696  3.901350   
2       BAZ1B   BAZ1B  2.710669  2.811728  2.876774  3.168661  3.043015   
3       CALB1   CALB1  0.000000  0.000000  0.000000  0.175910  0.013266   
4        CAMP    CAMP  0.000000  0.000000  0.000000  0.000000  0.000000   
...       ...     ...       ...       ...       ...       ...       ...   
31661  ZYG11A  ZYG11A  0.967755  0.726847  0.889493  0.790267  0.855293   
31662  ZYG11B  ZYG11B  2.293320  2.246478  2.411234  2.700759  2.140013   
31663     ZYX     ZYX  3.887496  4.214949  4.037092  3.998899  4.406863   
31664   ZZEF1   ZZEF1  2.343738  2.260324  2.319413  2.628510  2.474490   
31665    ZZZ3    ZZZ3  2.559174  2.570475  2.624356  2.836952  2.813574   

            609       333       334       424       513       594       692  \
0      4.012899  4.301917  4.650650  4.664375  5.141932  4.452997  4.763295   
1      3.797594  4.074051  4.090701  4.164119  4.285950  4.606774  3.980290   
2      2.571048  3.137146  3.250937  3.556331  3.797231  3.622649  3.241692   
3      0.029345  0.000000  0.024565  0.031599  0.046796  0.000000  0.050790   
4      0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.375822   
...         ...       ...       ...       ...       ...       ...       ...   
31661  0.968751  0.461426  0.292139  0.177423  0.137982  0.247094  0.171427   
31662  2.374177  2.203580  2.200275  2.280068  2.719985  2.728458  2.495959   
31663  3.751839  4.510570  4.940148  5.035791  5.296190  4.915038  4.032330   
31664  2.055078  2.671848  2.934149  2.880033  2.722278  3.166945  2.696032   
31665  2.744224  2.946907  2.911308  3.120435  3.323893  3.136866  3.209207   

            713       723       778       803  
0      4.491629  4.741003  4.702408  4.591865  
1      4.372151  3.441566  3.905524  3.752139  
2      3.613331  3.145921  3.430839  3.312860  
3      0.021092  0.053470  0.061843  0.119192  
4      0.074674  0.000000  0.161390  0.000000  
...         ...       ...       ...       ...  
31661  0.138505  0.370853  0.131186  0.258032  
31662  2.794089  2.658116  2.628106  2.742500  
31663  4.463819  3.383870  4.126015  3.881900  
31664  3.145700  2.492015  2.960132  2.909808  
31665  3.074877  3.262778  3.158476  3.128059  

[31666 rows x 18 columns]

In [10]:
ih = pd.DataFrame()
ih["ArrayID"] = surv["GEO.Sample.number"]
ih["ArrayHeader"] = surv["GEO.Sample.number"]
ih["ClinicalHeader"] = surv["Barcode"]
ih

ArrayID  ArrayHeader ClinicalHeader
0       168          168  CB168 / 03TTM
1       461          461  CB461 / 03VCK
2       508          508  CB508 / 03VEX
3       520          520  CB520 / 03VFP
4       527          527  CB527 / 03VLS
5       609          609  CB609 / 03QDN
6       333          333  CB334 / 03UHU
7       334          334  CB333 / 03UHT
8       424          424  CB426 / 03UVF
9       513          513  CB513 / 03VEW
10      594          594  CB594 / 03W34
11      692          692  CB692 / 03WP3
12      713          713  CB713 / 03X0K
13      723          723  CB723 / 03W9K
14      778          778  CB778 / 03X3B
15      803          803  CB803 / 03X2Z

In [24]:
surv = pd.DataFrame(pd.read_csv("metadata.csv", sep = ",", header=0))
arrayid = surv.pop("GEO.Sample.number")
surv.insert(0, 'status', "")
surv.insert(0, 'time', "")
surv.insert(0, 'ArrayId', arrayid)
surv.columns = ['ArrayId', 'time', 'status', 'c title', 'c Sex', 'c Disease', 'c EosHPF']
surv

ArrayId time status        c title   c Sex    c Disease  c EosHPF
0       168              CB168 / 03TTM  female      control         0
1       461              CB461 / 03VCK    male      control         0
2       508              CB508 / 03VEX  female      control         0
3       520              CB520 / 03VFP    male      control         0
4       527              CB527 / 03VLS    male      control         0
5       609              CB609 / 03QDN  female      control         0
6       333              CB334 / 03UHU  female  EoE, active       267
7       334              CB333 / 03UHT    male  EoE, active       150
8       424              CB426 / 03UVF    male  EoE, active        67
9       513              CB513 / 03VEW  female  EoE, active        32
10      594              CB594 / 03W34    male  EoE, active       155
11      692              CB692 / 03WP3    male  EoE, active       173
12      713              CB713 / 03X0K    male  EoE, active        91
13      723              CB723 / 03W9K    male  EoE, active       343
14      778              CB778 / 03X3B  female  EoE, active       154
15      803              CB803 / 03X2Z  female  EoE, active       204

In [27]:
# Export files

path_dir = "./"
expr.to_csv(path_dir+'sherrill-EoE-expr.txt', header=True, index=False,sep='\t')
surv.to_csv(path_dir+"sherrill-EoE-survival.txt", header=True, index=False,sep='\t')
ih.to_csv(path_dir+"sherrill-EoE-ih.txt", header=True, index=False,sep='\t')

In [28]:
# Build idx file
path_dir = "./"

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'sherrill-EoE-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'sherrill-EoE-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
